# **Single Axis Helmholtz Coil Simulation**

Import Libraries

In [6]:
import numpy as np
import pandas as pd
import time
import parallel_test4 as test_3
import plotMagneticField as hplot

## **Simulate Helmholtz coils with Square in a single Axis**

Simulation Settings

In [7]:
# Initialize coil parameters
X_coil = test_3.CoilParameters(0.9954953419357395, 0.5864538565842049, 30)

# Current coil simulation
I = 1
# Rotation matriz
Ax = np.eye(3) ## eye rotation matrix

# Simulation settings
parallel_coils = 1
batch_Size = 40
grid_length_size = 0.01 #Space among evaluation points
num_seg = 300           #Numer of segments 

Set the spires Geometry

In [8]:
##Spawn spires
spire1_x_s, spire2_x_s = test_3.square_spires(Ax, X_coil.h, X_coil.a, num_seg)

f0 = None
f0 = hplot.plot_spires(f0, spire1_x_s, spire2_x_s, color='black')

# Plot the square spires
f0.show()

In [9]:
# Generar grid
X, Y, Z = test_3.generate_range(X_coil.a*3/4, grid_length_size)

hplot.plot_grid(X, Y, Z, f0)

## Run Simulations

In [ ]:
#Run simulations
start_time = time.time() #Count start time
x_coil_results_s = test_3.coil_simulation_1d_sequential(X, Y, Z, X_coil, I, spire1_x_s, spire2_x_s, parallel_coils, batch_Size)
end_time = time.time()   #Mark ending time

# Calcular la norma del campo magnético B = sqrt(Bx^2 + By^2 + Bz^2)
x_coil_results_s["B_norm"] = np.sqrt(x_coil_results_s["Bx"]**2 + x_coil_results_s["By"]**2 + x_coil_results_s["Bz"]**2)

#Calculate and show the simulation time
execution_time = end_time - start_time
print(f'Simulation finished in {execution_time/60} minutes...')

# Save results in a CSV file
output_file = 'x_coil_results_s.csv'
x_coil_results_s.to_csv(output_file, index=False)

Simulation Progress:   0%|          | 560/139538 [00:42<2:10:53, 17.70it/s]

## Plot the obtained results

In [2]:
# Read data from previous simulations
x_coil_results_s = pd.read_csv('x_coil_results_s.csv')

In [ ]:
hplot.simple_3d_surface_plot(x_coil_results_s,'Bx')

In [ ]:
hplot.simple_3d_surface_plot(x_coil_results_s,'By')

In [ ]:
hplot.simple_3d_surface_plot(x_coil_results_s,'Bz')

In [ ]:
hplot.simple_3d_surface_plot(x_coil_results_s,'B_norm')

In [ ]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np

# Load the dataset
df = pd.read_csv('x_coil_results_s.csv')

# Filter rows where Z = 0 (or another filter condition)
df = df[(df['Z'] == 0)]

# Filter out zero-magnitude vectors to avoid division by zero
df = df[df['B_norm'] > 0]

# Normalize the vector components
df['Bx_norm'] = df['Bx'] / df['B_norm']
df['By_norm'] = df['By'] / df['B_norm']
df['Bz_norm'] = df['Bz'] / df['B_norm']

# **CONTROL NUMBER OF ARROWS PLOTTED**
subsampling_factor = 1 # Change this to increase or decrease arrow density (higher = fewer arrows)
df = df.iloc[::subsampling_factor, :]  # Take every nth row


# Create a grid for the heatmap (use unique X and Y values)
x_unique = np.sort(df['X'].unique())
y_unique = np.sort(df['Y'].unique())

# Create an empty 2D array for the heatmap (Z=0 plane)
heatmap_z = np.zeros((len(y_unique), len(x_unique)))

# Fill the heatmap matrix with the average magnitude at each (X, Y)
for i, x_val in enumerate(x_unique):
    for j, y_val in enumerate(y_unique):
        subset = df[(df['X'] == x_val) & (df['Y'] == y_val)]
        if not subset.empty:
            heatmap_z[j, i] = subset['B_norm'].mean()  # Average if multiple values exist

# Create the figure
fig = go.Figure()

# Add the 3D Surface Heatmap (Z = 0 plane)
fig.add_trace(go.Surface(
    x=x_unique,
    y=y_unique,
    z=np.full_like(heatmap_z, 0),  # Position the heatmap at Z=0
    surfacecolor=heatmap_z,  # Use the magnitude values for coloring
    colorscale='Plasma',  # Heatmap color scale
    cmin=df['B_norm'].min(),
    cmax=df['B_norm'].max()/16,  # Adjust color scaling
    colorbar=dict(title='Heatmap Magnitude'),
    opacity=0.7,  # Adjust transparency
    showscale=True
))


# Add the Cone Plot for the vector field (with reduced arrows)
fig.add_trace(go.Cone(
    x=df['X'], y=df['Y'], z=df['Z'],
    u=df['Bx_norm'], v=df['By_norm'], w=df['Bz_norm'],
    colorscale=[[0, 'black'], [1, 'black']],  # Custom color scale
    showscale=False,
    sizemode="absolute",
    sizeref=20,  # Adjust arrow size
    anchor="tail"
))

# Configure the 3D scene to share the same frame
fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z',
        aspectmode='data',  # Ensures equal scaling for all axes
        camera_eye=dict(x=1.2, y=1.2, z=0.6),  # Adjust camera perspective
    )
)

fig = hplot.plot_spires(fig, spire1_x_s, spire2_x_s, color='black')

# Show the figure
fig.show()


In [ ]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from scipy.interpolate import griddata

# Load the dataset
df = pd.read_csv('x_coil_results_s.csv')

# Filter rows where Z = 0 (or another filter condition)
df = df[df['Z'] == 0]

# Find the reference value at (X=0, Y=0)
reference_point = df[(df['X'] == 0) & (df['Y'] == 0) & (df['Z'] == 0)]

if not reference_point.empty:
    reference_value = reference_point['B_norm'].values[0]
else:
    reference_value = df['B_norm'].mean()  # Fallback if (0,0) is not in the dataset

# Calcular el rango del 0.5% del valor máximo
tolerance = 0.005 * reference_value
lower_bound = reference_value - tolerance
upper_bound = reference_value + tolerance

# Filtrar los puntos que estén dentro de ese rango
filtered_points = df[(df['Bx'] >= lower_bound) & (df['Bx'] <= upper_bound)]

# Normalize the vector components
df['Bx_norm'] = df['Bx'] / df['B_norm']
df['By_norm'] = df['By'] / df['B_norm']
df['Bz_norm'] = df['Bz'] / df['B_norm']

# **CONTROL NUMBER OF ARROWS PLOTTED**
subsampling_factor = 1  # Reduce arrow density for clarity
df = df.iloc[::subsampling_factor, :]

# **Generate a smooth grid**
grid_x = np.linspace(df['X'].min(), df['X'].max(), 50)
grid_y = np.linspace(df['Y'].min(), df['Y'].max(), 50)
grid_xx, grid_yy = np.meshgrid(grid_x, grid_y)

# **Interpolate the magnitude values to make the surface smooth**
grid_zz = griddata(
    (df['X'], df['Y']), df['B_norm'], (grid_xx, grid_yy), method='cubic'
)

# Create the figure
fig = go.Figure()

# **Smooth 3D Surface (Heatmap)**
fig.add_trace(go.Surface(
    x=grid_x,
    y=grid_y,
    z=np.zeros_like(grid_zz),  # Keep the surface at Z=0
    surfacecolor=grid_zz,  # Use interpolated values for coloring
    colorscale='Plasma',  # Smooth colormap
    cmin=df['B_norm'].min(),
    cmax=df['B_norm'].max()/16,  # Use full range of values
    colorbar=dict(title='Magnetic Field Strength'),
    opacity=0.7,  # Transparency for better visibility
    showscale=True
))

# **Contour Region for Low Variation (<5%)**
# Agregar puntos en 3D
fig.add_trace(go.Scatter3d(
    x=filtered_points['X'], 
    y=filtered_points['Y'], 
    z=filtered_points['Z'],
    mode='markers',  # Solo puntos
    marker=dict(
        size=5,  # Tamaño de los puntos
        color='blue',  # Color de los puntos
        opacity=0.8  # Opacidad de los puntos
    ),
    name="Puntos en 3D"
))

fig.add_trace(go.Mesh3d(
    x=filtered_points['X'],
    y=filtered_points['Y'],
    z=filtered_points['Z'],
    opacity=0.3,
    color='grey',
    alphahull=5,  # Creates a smooth convex hull
    name="Low Variation (<0.5%) Region"
))

# **Add the Cone Plot for the vector field (with reduced arrows)**
fig.add_trace(go.Cone(
    x=df['X'], y=df['Y'], z=df['Z'],
    u=df['Bx_norm'], v=df['By_norm'], w=df['Bz_norm'],
    colorscale=[[0, 'black'], [1, 'black']],  # Custom color
    showscale=False,
    sizemode="absolute",
    sizeref=20,  # Adjust arrow size
    anchor="tail"
))

# Configure the 3D scene
fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z',
        aspectmode='data',  # Ensures equal scaling for all axes
        camera_eye=dict(x=1.2, y=1.2, z=0.6),
    )
)

fig = hplot.plot_spires(fig, spire1_x_s, spire2_x_s, color='black')

# Show the figure
fig.show()
